In [2]:
from tqdm.auto import tqdm
import pandas as pd
import numpy as np
import warnings
import optuna
import os

In [3]:
PATH_DATA = "./data"
train = pd.read_csv(os.path.join(PATH_DATA, 'new_train_big_2.csv'), index_col='client_id')
test = pd.read_csv(os.path.join(PATH_DATA, 'new_test_big_2.csv'), index_col='client_id')
gender_train = pd.read_csv(os.path.join(PATH_DATA, 'train.csv'), index_col='client_id')

# Find common columns
common_columns = train.columns.intersection(test.columns)
train = train[common_columns]

X = train.copy()
y = train.join(gender_train, how='inner')['gender']

### Катбуст и ЛГБМ учили на с кросс-валидацией. В иксджибуст в виду тех. ограничений сделали трейн-тест-сплит и оценили перфоманс на окросс-валидации. Все три модели сохранили в .pkl

    CatBoost    

In [4]:
from catboost import CatBoostClassifier, Pool, cv

with warnings.catch_warnings(): 
    warnings.simplefilter("ignore")
    
    def objective(trial):
        param = {
            'depth': trial.suggest_int('depth', 5, 7),  # было 6, теперь от 5 до 7
            'learning_rate': trial.suggest_float('learning_rate', 0.02, 0.04, step=0.01),  # было 0.03, теперь от 0.02 до 0.04 с шагом 0.01
            'iterations': trial.suggest_int('iterations', 950, 1050, step=50),  # было 1000, теперь от 950 до 1050 с шагом 50
            'l2_leaf_reg': trial.suggest_int('l2_leaf_reg', 8, 10),  # было 9, теперь от 8 до 10
            'min_data_in_leaf': trial.suggest_int('min_data_in_leaf', 1, 3),  # было 2, теперь от 1 до 3
            'loss_function': trial.suggest_categorical('loss_function', ['Logloss']),  # не изменилось
            'eval_metric': trial.suggest_categorical('eval_metric', ['AUC'])  # не изменилось
        }

        pool = Pool(X, y)

        cv_results = cv(pool=pool,
                        params=param,
                        fold_count=5,
                        early_stopping_rounds=10,
                        iterations=650,
                        stratified=True,
                        partition_random_seed=12,
                        plot=False)

        best_score = np.max(cv_results['test-AUC-mean'])
        return best_score

    with warnings.catch_warnings():
        warnings.simplefilter("ignore")

        study = optuna.create_study(direction='maximize')
        with tqdm(total=40) as pbar:
            def callback(study, trial):
                pbar.update(1)

            study.optimize(objective, n_trials=40, callbacks=[callback])

print('Best parameters:', study.best_params)

CB_best_params = study.best_params
train_pool = Pool(X, y)
catboost_model = CatBoostClassifier(**CB_best_params)
catboost_model.fit(train_pool)



[I 2023-11-21 18:30:53,682] A new study created in memory with name: no-name-389e6c26-bda2-49ba-b8e0-4990d9b7594e


  0%|          | 0/50 [00:00<?, ?it/s]

Training on fold [0/5]
0:	test: 0.7729153	best: 0.7729153 (0)	total: 66.1ms	remaining: 42.9s
1:	test: 0.7889965	best: 0.7889965 (1)	total: 83.9ms	remaining: 27.2s
2:	test: 0.7980949	best: 0.7980949 (2)	total: 83.9ms	remaining: 27.2s
3:	test: 0.8005431	best: 0.8005431 (3)	total: 2.39s	remaining: 8m 35s
4:	test: 0.8045107	best: 0.8045107 (4)	total: 2.41s	remaining: 6m 28s
5:	test: 0.8124001	best: 0.8124001 (5)	total: 2.43s	remaining: 5m 12s
6:	test: 0.8148137	best: 0.8148137 (6)	total: 2.44s	remaining: 4m 21s
7:	test: 0.8166852	best: 0.8166852 (7)	total: 2.46s	remaining: 3m 45s
8:	test: 0.8187929	best: 0.8187929 (8)	total: 2.48s	remaining: 3m 18s
9:	test: 0.8251433	best: 0.8251433 (9)	total: 2.49s	remaining: 2m 57s
10:	test: 0.8249850	best: 0.8251433 (9)	total: 2.51s	remaining: 2m 40s
11:	test: 0.8269564	best: 0.8269564 (11)	total: 2.53s	remaining: 2m 26s
12:	test: 0.8275375	best: 0.8275375 (12)	total: 2.54s	remaining: 2m 15s
13:	test: 0.8265717	best: 0.8275375 (12)	total: 2.56s	remainin

[I 2023-11-21 18:31:23,789] Trial 0 finished with value: 0.8785554555326958 and parameters: {'depth': 5, 'learning_rate': 0.03, 'iterations': 1050, 'l2_leaf_reg': 10, 'min_data_in_leaf': 2, 'loss_function': 'Logloss', 'eval_metric': 'AUC'}. Best is trial 0 with value: 0.8785554555326958.


463:	test: 0.8941785	best: 0.8941874 (460)	total: 7.31s	remaining: 3.08s
464:	test: 0.8941182	best: 0.8941874 (460)	total: 7.33s	remaining: 3.06s
465:	test: 0.8940313	best: 0.8941874 (460)	total: 7.35s	remaining: 3.04s
466:	test: 0.8940189	best: 0.8941874 (460)	total: 7.36s	remaining: 3.03s
467:	test: 0.8938717	best: 0.8941874 (460)	total: 7.38s	remaining: 3.01s
468:	test: 0.8939178	best: 0.8941874 (460)	total: 7.4s	remaining: 3s
469:	test: 0.8939639	best: 0.8941874 (460)	total: 7.41s	remaining: 2.98s
470:	test: 0.8939320	best: 0.8941874 (460)	total: 7.42s	remaining: 2.96s

bestTest = 0.8941873829
bestIteration = 460

Training on fold [0/5]
0:	test: 0.7728517	best: 0.7728517 (0)	total: 22.2ms	remaining: 14.4s
1:	test: 0.7889717	best: 0.7889717 (1)	total: 39.5ms	remaining: 12.8s
2:	test: 0.7931862	best: 0.7931862 (2)	total: 58.1ms	remaining: 12.5s
3:	test: 0.7967770	best: 0.7967770 (3)	total: 77.4ms	remaining: 12.5s
4:	test: 0.8025676	best: 0.8025676 (4)	total: 96.5ms	remaining: 12.5s
5

...

305:	test: 0.8896202	best: 0.8897249 (298)	total: 38.4s	remaining: 44.7s
306:	test: 0.8895528	best: 0.8897249 (298)	total: 38.5s	remaining: 44.5s
307:	test: 0.8895244	best: 0.8897249 (298)	total: 38.5s	remaining: 44.2s
308:	test: 0.8896575	best: 0.8897249 (298)	total: 38.6s	remaining: 44s

bestTest = 0.8897248709
bestIteration = 298

Training on fold [0/5]
0:	test: 0.7722794	best: 0.7722794 (0)	total: 33.4ms	remaining: 21.7s
1:	test: 0.7994755	best: 0.7994755 (1)	total: 59.4ms	remaining: 19.2s
2:	test: 0.8084271	best: 0.8084271 (2)	total: 93.2ms	remaining: 20.1s
3:	test: 0.8146881	best: 0.8146881 (3)	total: 123ms	remaining: 19.8s
4:	test: 0.8197127	best: 0.8197127 (4)	total: 166ms	remaining: 21.4s
5:	test: 0.8245516	best: 0.8245516 (5)	total: 166ms	remaining: 21.4s
6:	test: 0.8254298	best: 0.8254298 (6)	total: 202ms	remaining: 21.6s
7:	test: 0.8275596	best: 0.8275596 (7)	total: 2.52s	remaining: 3m 51s
8:	test: 0.8276428	best: 0.8276428 (8)	total: 2.56s	remaining: 3m 24s
9:	test: 0.8255

[I 2023-11-21 19:22:33,185] Trial 38 finished with value: 0.8798851102774154 and parameters: {'depth': 6, 'learning_rate': 0.03, 'iterations': 1050, 'l2_leaf_reg': 8, 'min_data_in_leaf': 1, 'loss_function': 'Logloss', 'eval_metric': 'AUC'}. Best is trial 5 with value: 0.8807891804333648.


345:	test: 0.8922364	best: 0.8923765 (337)	total: 40.9s	remaining: 37.2s
346:	test: 0.8922825	best: 0.8923765 (337)	total: 40.9s	remaining: 37s
347:	test: 0.8922133	best: 0.8923765 (337)	total: 41s	remaining: 36.8s

bestTest = 0.8923764828
bestIteration = 337

Training on fold [0/5]
0:	test: 0.7728941	best: 0.7728941 (0)	total: 44.3ms	remaining: 28.7s
1:	test: 0.7890071	best: 0.7890071 (1)	total: 61.4ms	remaining: 19.9s
2:	test: 0.7934656	best: 0.7934656 (2)	total: 77.6ms	remaining: 16.7s
3:	test: 0.7970105	best: 0.7970105 (3)	total: 96.6ms	remaining: 15.6s
4:	test: 0.8025587	best: 0.8025587 (4)	total: 113ms	remaining: 14.6s
5:	test: 0.8096450	best: 0.8096450 (5)	total: 132ms	remaining: 14.2s
6:	test: 0.8114811	best: 0.8114811 (6)	total: 154ms	remaining: 14.2s
7:	test: 0.8126548	best: 0.8126548 (7)	total: 172ms	remaining: 13.8s
8:	test: 0.8137559	best: 0.8137559 (8)	total: 187ms	remaining: 13.3s
9:	test: 0.8140478	best: 0.8140478 (9)	total: 203ms	remaining: 13s
10:	test: 0.8153789	best

[I 2023-11-21 19:23:07,908] Trial 39 finished with value: 0.8690872934557035 and parameters: {'depth': 5, 'learning_rate': 0.02, 'iterations': 950, 'l2_leaf_reg': 9, 'min_data_in_leaf': 3, 'loss_function': 'Logloss', 'eval_metric': 'AUC'}. Best is trial 5 with value: 0.8807891804333648.


638:	test: 0.8933928	best: 0.8934070 (637)	total: 8.25s	remaining: 145ms
639:	test: 0.8934779	best: 0.8934779 (639)	total: 8.25s	remaining: 145ms
640:	test: 0.8934992	best: 0.8934992 (640)	total: 8.26s	remaining: 119ms
641:	test: 0.8935045	best: 0.8935045 (641)	total: 8.28s	remaining: 106ms
642:	test: 0.8935187	best: 0.8935187 (642)	total: 8.29s	remaining: 92.4ms
643:	test: 0.8935613	best: 0.8935613 (643)	total: 8.29s	remaining: 92.4ms
644:	test: 0.8936216	best: 0.8936216 (644)	total: 8.3s	remaining: 66ms
645:	test: 0.8936109	best: 0.8936216 (644)	total: 8.32s	remaining: 52.8ms
646:	test: 0.8936429	best: 0.8936429 (646)	total: 8.33s	remaining: 39.6ms
647:	test: 0.8937191	best: 0.8937191 (647)	total: 8.35s	remaining: 26.4ms
648:	test: 0.8938327	best: 0.8938327 (648)	total: 8.36s	remaining: 13.2ms
649:	test: 0.8938114	best: 0.8938327 (648)	total: 8.37s	remaining: 0us

bestTest = 0.8938326523
bestIteration = 648

Best parameters: {'depth': 6, 'learning_rate': 0.04, 'iterations': 1000, 'l2

    LightGBM

In [7]:
import lightgbm as lgb

with warnings.catch_warnings():
    warnings.simplefilter("ignore")

    def objective(trial):
        param = {
            "objective": "binary",
            "metric": "binary_error",
            "verbosity": -1,
            "boosting_type": "gbdt",
            "seed": 12,
            'lambda_l1': trial.suggest_float('lambda_l1', 3.0, 4.0),   
            'lambda_l2': trial.suggest_float('lambda_l2', 0.1, 0.3),  
            'num_leaves': trial.suggest_int('num_leaves', 220, 250),   
            'feature_fraction': trial.suggest_float('feature_fraction', 0.15, 0.2),   
            'bagging_fraction': trial.suggest_float('bagging_fraction', 0.85, 0.9),  
            'bagging_freq': trial.suggest_int('bagging_freq', 10, 15),   
            'min_child_samples': trial.suggest_int('min_child_samples', 30, 40),   
            'max_depth': trial.suggest_int('max_depth', 2, 5),   
            "device": "gpu"
        }
        
        num_boost_round = trial.suggest_int('num_boost_round', 580, 630)

        cv_results = lgb.cv(param, lgb.Dataset(X, label=y), num_boost_round=num_boost_round, nfold=5, stratified=True,
                            metrics='auc', seed=12)
        best_auc = max(cv_results['valid auc-mean'])
        return best_auc

    study = optuna.create_study(direction='maximize')

    with tqdm(total=40) as pbar:
        def callback(study, trial):
            pbar.update(1)

        study.optimize(objective, n_trials=40, callbacks=[callback])

print('Best parameters:', study.best_params)

best_params_lgbm = study.best_params
best_num_boost_round = best_params_lgbm.pop('num_boost_round')
full_train_set_lgbm = lgb.Dataset(X, label=y)
lgbm_final_model = lgb.train(best_params_lgbm, full_train_set_lgbm, num_boost_round=best_num_boost_round) #Best is trial 32 with value: 0.8820998894589097

[I 2023-11-21 19:33:17,413] A new study created in memory with name: no-name-b9e84c53-2f6d-4f15-aad9-451ca9b5f5ad


  0%|          | 0/40 [00:00<?, ?it/s]

[I 2023-11-21 19:33:35,658] Trial 0 finished with value: 0.8822620367311081 and parameters: {'lambda_l1': 3.527013169098509, 'lambda_l2': 0.12033532471567543, 'num_leaves': 250, 'feature_fraction': 0.15034150298232432, 'bagging_fraction': 0.8670591486409043, 'bagging_freq': 15, 'min_child_samples': 32, 'max_depth': 4, 'num_boost_round': 587}. Best is trial 0 with value: 0.8822620367311081.
[I 2023-11-21 19:33:47,179] Trial 1 finished with value: 0.8823486902360086 and parameters: {'lambda_l1': 3.796591936937903, 'lambda_l2': 0.20710618051506058, 'num_leaves': 230, 'feature_fraction': 0.1743761994240506, 'bagging_fraction': 0.8797245935429774, 'bagging_freq': 10, 'min_child_samples': 39, 'max_depth': 3, 'num_boost_round': 616}. Best is trial 1 with value: 0.8823486902360086.
[I 2023-11-21 19:34:08,887] Trial 2 finished with value: 0.8813642142408586 and parameters: {'lambda_l1': 3.7809901591212594, 'lambda_l2': 0.15790806369057192, 'num_leaves': 232, 'feature_fraction': 0.19406524014110

Best parameters: {'lambda_l1': 3.0074717981967725, 'lambda_l2': 0.24500713012255412, 'num_leaves': 240, 'feature_fraction': 0.19779451838807108, 'bagging_fraction': 0.8524907254966303, 'bagging_freq': 12, 'min_child_samples': 30, 'max_depth': 2, 'num_boost_round': 628}
[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.027095 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 70668
[LightGBM] [Info] Number of data points in the train set: 7560, number of used features: 310
[LightGBM] [Info] Start training from score 0.444577
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning]

    XGBoost

In [10]:
import xgboost as xgb
from sklearn.metrics import roc_auc_score
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=12)

def objective(trial):
    param = {
        'tree_method': 'gpu_hist',  # Using GPU
        'learning_rate': trial.suggest_float('learning_rate', 0.02, 0.06),
        'n_estimators': trial.suggest_int('n_estimators', 500, 700),
        'max_depth': trial.suggest_int('max_depth', 4, 8),
        'min_child_weight': trial.suggest_float('min_child_weight', 0.1, 0.6),
        'gamma': trial.suggest_float('gamma', 0, 0.1),
        'subsample': trial.suggest_float('subsample', 0.7, 0.9),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 0.7),
        'scale_pos_weight': trial.suggest_float('scale_pos_weight', 0.8, 1.2),
        'seed': 12
    }

    model = xgb.XGBClassifier(**param)
    model.fit(X_train, y_train, eval_set=[(X_test, y_test)], early_stopping_rounds=100, verbose=False)
    preds = model.predict_proba(X_test)[:, 1]
    roc_auc = roc_auc_score(y_test, preds)
    return roc_auc

# Number of trials
n_trials = 50

# Initialize tqdm progress bar
with tqdm(total=n_trials) as pbar:
    
    # Callback to update progress after each trial
    def update_progress(study, trial):
        pbar.update(1)

    # Suppress warnings
    with warnings.catch_warnings():
        warnings.simplefilter("ignore")

        # Creating the study object and running optimization
        study = optuna.create_study(direction='maximize')
        study.optimize(objective, n_trials=n_trials, callbacks=[update_progress])

    print('Лучшие параметры:', study.best_params)


  0%|          | 0/50 [00:00<?, ?it/s]

[I 2023-11-21 19:44:04,776] A new study created in memory with name: no-name-0399cbd1-a229-478d-9c0a-2aa4945c5307
[I 2023-11-21 19:44:08,765] Trial 0 finished with value: 0.8746824933766488 and parameters: {'learning_rate': 0.03223682887984087, 'n_estimators': 652, 'max_depth': 7, 'min_child_weight': 0.39025479626471327, 'gamma': 0.08646216739960286, 'subsample': 0.7459854369632812, 'colsample_bytree': 0.6348859264886311, 'scale_pos_weight': 1.1004400277739332}. Best is trial 0 with value: 0.8746824933766488.
[I 2023-11-21 19:44:11,549] Trial 1 finished with value: 0.8736283978276467 and parameters: {'learning_rate': 0.04787777916666289, 'n_estimators': 665, 'max_depth': 7, 'min_child_weight': 0.2937493725845943, 'gamma': 0.09447393960620704, 'subsample': 0.8906680039108863, 'colsample_bytree': 0.6160930933845907, 'scale_pos_weight': 1.1693761567631975}. Best is trial 0 with value: 0.8746824933766488.
[I 2023-11-21 19:44:14,581] Trial 2 finished with value: 0.8803971719215739 and param

Лучшие параметры: {'learning_rate': 0.05072509919915307, 'n_estimators': 623, 'max_depth': 4, 'min_child_weight': 0.1837248208913841, 'gamma': 0.021193623675200213, 'subsample': 0.8034007511045221, 'colsample_bytree': 0.6815225992761035, 'scale_pos_weight': 1.1244119312365564}


In [17]:
def cv_score(params, train, y_true):
    cv_res=xgb.cv(params, xgb.DMatrix(train, y_true),
                  early_stopping_rounds=10, maximize=True,
                  num_boost_round=10000, nfold=5, stratified=True, metrics=['auc'])
    index_argmax = cv_res['test-auc-mean'].argmax()
    print('Cross-validation, ROC AUC: {:.3f}+-{:.3f}, Trees: {}'.format(cv_res.loc[index_argmax]['test-auc-mean'],
                                                                        cv_res.loc[index_argmax]['test-auc-std'],

                                                                        index_argmax))

best_params = study.best_params
cv_score(best_params, train=X, y_true=y)

XGB_final_model = xgb.XGBClassifier(**best_params)
XGB_final_model.fit(X, y, verbose=True)

/home/veidlink/miniforge3/lib/python3.10/site-packages/xgboost/core.py:160: UserWarning: [19:47:44] WARNING: /workspace/src/learner.cc:742: 
Parameters: { "n_estimators" } are not used.

  warnings.warn(smsg, UserWarning)


Cross-validation, ROC AUC: 0.870+-0.008, Trees: 256


XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.6815225992761035, device=None,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, feature_types=None, gamma=0.021193623675200213,
              grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=0.05072509919915307,
              max_bin=None, max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=4, max_leaves=None,
              min_child_weight=0.1837248208913841, missing=nan,
              monotone_constraints=None, multi_strategy=None, n_estimators=623,
              n_jobs=None, num_parallel_tree=None, random_state=None, ...)

Сохраняем модели

In [18]:
import joblib

joblib.dump(XGB_final_model, 'XGB_final_model.pkl')
joblib.dump(lgbm_final_model, 'LGBM_best_model.pkl')
joblib.dump(catboost_model, 'CB_final_model.pkl')

['CB_final_model.pkl']